In [1]:
import pandas as pd
import json
import requests
import aiohttp
import asyncio

## Getting surfline spots

Taken from [ovalwood](https://github.com/ovalwood/surf_locations) and adapted to run a bit faster with async


In [2]:
response = requests.get("https://services.surfline.com/taxonomy?type=taxonomy&id=58f7ed51dadb30820bb3879c&maxDepth=0")
json_data = response.json()
json_contains = json_data['contains']
states = []
state_ids = []
state_urls = []
for x in json_contains:
    states.append(x['name'])
    state_ids.append(x['_id'])


In [3]:

for state_id in state_ids:
    state_urls.append("https://services.surfline.com/taxonomy?type=taxonomy&id=" + state_id + "&maxDepth=0")
   

In [4]:
async def fetch(url, session):
    async with session.get(url) as response:
        return await response.json()

async def fetch_all(urls):
    data = []
    async with aiohttp.ClientSession() as session:
        tasks = []
        for url in urls:
            tasks.append(fetch(url, session))
        data = await asyncio.gather(*tasks)
    return data

In [5]:
state_data = await fetch_all(state_urls)

In [7]:
county_ids = []    
for state in state_data:
    state_contains = state['contains']
    for y in state_contains:
        county_ids.append(y['_id'])
      

In [8]:
county_urls = []
for county_id in county_ids:
    county_urls.append("https://services.surfline.com/taxonomy?type=taxonomy&id=" + county_id + "&maxDepth=0")


In [9]:

county_data = await fetch_all(county_urls)

[{'_id': '58f7ee46dadb30820bb499a7',
  'geonameId': 4185838,
  'type': 'geoname',
  'liesIn': ['58f7ee46dadb30820bb49998'],
  'geonames': {'fcode': 'ADM2',
   'lat': '30.92249',
   'adminName1': 'Georgia',
   'fcodeName': 'second-order administrative division',
   'countryName': 'United States',
   'fclName': 'country, state, region,...',
   'name': 'Camden County',
   'countryCode': 'US',
   'population': 50513,
   'fcl': 'A',
   'countryId': '6252001',
   'toponymName': 'Camden County',
   'geonameId': 4185838,
   'lng': '-81.63639',
   'adminCode1': 'GA'},
  'location': {'coordinates': [-81.63639, 30.92249], 'type': 'Point'},
  'enumeratedPath': ',Earth,North America,United States,Georgia,Camden County',
  'name': 'Camden County',
  'category': 'geonames',
  'hasSpots': True,
  'associated': {'links': [{'key': 'taxonomy',
     'href': 'http://spots-api.prod.surfline.com/taxonomy?id=4185838&type=geoname'},
    {'key': 'www',
     'href': 'https://www.surfline.com/surf-reports-forecas

In [11]:
region_ids = []
region_names = []
for county in county_data:
    county_contains = county['contains']
    for z in county_contains:
        region_ids.append(z['_id'])
        region_names.append(z['name'])
    

In [12]:
region_urls = []
for region_id in region_ids:
    region_urls.append("https://services.surfline.com/taxonomy?type=taxonomy&id=" + region_id + "&maxDepth=0")


In [13]:
region_data = await fetch_all(region_urls)

In [14]:
spot_ids = []
spot_names = []
spot_lon = []
spot_lat = []
spot_urls = []


In [15]:

for region in region_data:
    region_contains = region['contains']
    if len(region_contains) == 0:
        spot_ids.append(region['_id'])
        spot_names.append(region['name'])
        region_associated = region['associated']
        region_links = region_associated['links']
        region_location = region['location']
        region_coordinates = region_location['coordinates']
        spot_lon.append(region_coordinates[0])
        spot_lat.append(region_coordinates[1])
        for i in region_links:
            if i['key'] == "www":
                spot_urls.append(i['href'])

In [16]:
df = pd.DataFrame({"ids": spot_ids, "names": spot_names, "lon": spot_lon, "lat": spot_lat, "urls": spot_urls})
df.to_csv('./data/spot_list.csv')

In [17]:
df.head()

ids                  names        lon        lat  \
0  58f7ee46dadb30820bb499b6         Kings Bay Base -81.565890  30.798360   
1  58f7ee49dadb30820bb49d88    Harbor Marker Buoys -81.325124  31.162128   
2  58f7ee4adadb30820bb49e3f             Sea Island -81.326290  31.200763   
3  58f7ee51dadb30820bb4a583  St. Catherines Island -81.133284  31.625357   
4  58f7ee4fdadb30820bb4a400      Blackbeard Island -81.210006  31.466844   

                                                urls  
0  https://www.surfline.com/surf-reports-forecast...  
1  https://www.surfline.com/surf-report/harbor-ma...  
2  https://www.surfline.com/surf-report/sea-islan...  
3  https://www.surfline.com/surf-report/st-cather...  
4  https://www.surfline.com/surf-report/blackbear...

In [18]:
df.shape

(1320, 5)